# Winter 2022 and 2023 Precipitation and Wind Characteristics

Author: Daniel Hogan
Created: January 17, 2024

This notebook will look at wind speed, direction, and precipitation to deduce how winds and precipitatiopn are related. This will help provide evidence in support (or against) my hypothesis that less snow means less sublimation, even if it is windy.

### Imports

In [1]:
# general
import os
import glob
import datetime as dt
import json
# data 
import xarray as xr 
from sublimpy import utils, variables, tidy, turbulence
import numpy as np
import pandas as pd
from act import discovery, plotting
# plotting
import matplotlib.pyplot as plt
from metpy.cbook import get_test_data
from metpy.plots import add_metpy_logo, SkewT
import plotly.express as px 
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.io as pio
# helper tools
from scripts.get_sail_data import get_sail_data
from scripts.helper_funcs import create_windrose_df, simple_sounding, mean_sounding
import scripts.helper_funcs as hf
from metpy import calc, units
import scipy.stats as stats
from sklearn.linear_model import LinearRegression
import time
# make plotly work 
init_notebook_mode(connected=True)
cf.go_offline()

nctoolkit is using Climate Data Operators version 2.3.0


# Laser Disdrometer data
Here, I will gather the laser disdrometer data and organize it into hourly data to plot alongside wind speeds and direction.

In [2]:
# gather laser disdrometer data for 2023
w23_ld_mtcb_ds = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/sail_data/winter_22_23/laser_disdrometer_mt_cb_20221001_20230930.nc')
w23_ld_gts_ds = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/sail_data/winter_22_23/laser_disdrometer_gothic_20221001_20230930.nc')

# gather laser disdrometer data for 2022
w22_ld_mtcb_ds = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/sail_data/winter_21_22/laser_disdrometer_mt_cb_20211001_20220930.nc')
w22_ld_gts_ds = xr.open_dataset('/storage/dlhogan/synoptic_sublimation/sail_data/winter_21_22/laser_disdrometer_gothic_20211001_20220930.nc')

Laser disdrometer is 1 minute data, with other dimensions of particle size (mm) and raw_fall_velocity (m/s).
The variable of interest is `precip_rate` and `qc_precip_rate`

In [3]:
# Now let's filtter the data to our winter period (Dec 1 - Mar 31) and only look at the precip_rate data
w23_prcp_rate_mtcb_ds = w23_ld_mtcb_ds.sel(time=slice('2022-12-01', '2023-03-31'))[['precip_rate', 'qc_precip_rate']]
w23_prcp_rate_gts_ds = w23_ld_gts_ds.sel(time=slice('2022-12-01', '2023-03-31'))[['precip_rate', 'qc_precip_rate']]
w22_prcp_rate_mtcb_ds = w22_ld_mtcb_ds.sel(time=slice('2021-12-01', '2022-03-31'))[['precip_rate', 'qc_precip_rate']]
w22_prcp_rate_gts_ds = w22_ld_gts_ds.sel(time=slice('2021-12-01', '2022-03-31'))[['precip_rate', 'qc_precip_rate']]

In [4]:
# Now let's filter any data that has a qc_precip_rate value of 0
w23_prcp_rate_mtcb_ds = w23_prcp_rate_mtcb_ds.where(w23_prcp_rate_mtcb_ds.qc_precip_rate == 0, np.nan)
w23_prcp_rate_gts_ds = w23_prcp_rate_gts_ds.where(w23_prcp_rate_gts_ds.qc_precip_rate == 0, np.nan)
w22_prcp_rate_mtcb_ds = w22_prcp_rate_mtcb_ds.where(w22_prcp_rate_mtcb_ds.qc_precip_rate == 0, np.nan)
w22_prcp_rate_gts_ds = w22_prcp_rate_gts_ds.where(w22_prcp_rate_gts_ds.qc_precip_rate == 0, np.nan)
# now let's resample the data to hourly sums
w23_prcp_rate_1H_mtcb_ds = w23_prcp_rate_mtcb_ds.resample(time='1H').sum()/60
w23_prcp_rate_1H_gts_ds = w23_prcp_rate_gts_ds.resample(time='1H').sum()/60
w22_prcp_rate_1H_mtcb_ds = w22_prcp_rate_mtcb_ds.resample(time='1H').sum()/60
w22_prcp_rate_1H_gts_ds = w22_prcp_rate_gts_ds.resample(time='1H').sum()/60

2022

In [5]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=w22_prcp_rate_1H_mtcb_ds.time,
                         y=w22_prcp_rate_1H_mtcb_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Mt. Crested Butte'))
fig.add_trace(go.Scatter(x=w22_prcp_rate_1H_gts_ds.time,
                         y=w22_prcp_rate_1H_gts_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Gothic Townsite'))
fig.update_layout(title='Winter Precipitation (Dec 1 - Mar 31) 2021-2022',
                    xaxis_title='Time',
                    yaxis_title='Precipitation Rate (mm/hr)',
                    height=600,
                    width=800)

# add a second y-axis
fig.update_layout(yaxis2=dict(title='Cumulative Precipitation (mm)',
                              overlaying='y',
                              side='right'))
fig.add_trace(go.Scatter(x=w22_prcp_rate_1H_mtcb_ds.time,
                            y=w22_prcp_rate_1H_mtcb_ds.precip_rate.cumsum(),
                            mode='lines',
                            marker=dict(size=5,
                                        color='blue'),
                            name='Mt. Crested Butte',
                            showlegend=False,
                            yaxis='y2'))
fig.add_trace(go.Scatter(x=w22_prcp_rate_1H_gts_ds.time,
                            y=w22_prcp_rate_1H_gts_ds.precip_rate.cumsum(),
                            mode='lines',
                            marker=dict(size=5,
                                        color='red'),
                            name='Gothic Townsite',
                            showlegend=False,
                            yaxis='y2'))
# move the legend up a bit
fig.update_layout(legend=dict(y=1.2))

2023

In [6]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_mtcb_ds.time,
                         y=w23_prcp_rate_1H_mtcb_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Mt. Crested Butte'))
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_gts_ds.time,
                         y=w23_prcp_rate_1H_gts_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Gothic Townsite'))
fig.update_layout(title='Winter Precipitation (Dec 1 - Mar 31) 2022-2023',
                    xaxis_title='Time',
                    yaxis_title='Precipitation Rate (mm/hr)',
                    height=600,
                    width=800)

# add a second y-axis
fig.update_layout(yaxis2=dict(title='Cumulative Precipitation (mm)',
                              overlaying='y',
                              side='right'))
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_mtcb_ds.time,
                            y=w23_prcp_rate_1H_mtcb_ds.precip_rate.cumsum(),
                            mode='lines',
                            marker=dict(size=5,
                                        color='blue'),
                            name='Mt. Crested Butte',
                            showlegend=False,
                            yaxis='y2'))
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_gts_ds.time,
                            y=w23_prcp_rate_1H_gts_ds.precip_rate.cumsum(),
                            mode='lines',
                            marker=dict(size=5,
                                        color='red'),
                            name='Gothic Townsite',
                            showlegend=False,
                            yaxis='y2'))
# move the legend up a bit
fig.update_layout(legend=dict(y=1.2))

### Wind Data
Now, let's grab the SOS data, the SAIL met data, and the SPLASH data and add the precipitation data to each

In [7]:
# Now let's grab wind data from SOS for 2023 at Kettle Ponds and wind data from SAIL at Gothic
sos_1H_max_wspd_ds = xr.open_dataset('../../01_data/processed_data/sos_ds_1H_max_wspd_storage.nc')
sos_1H_mean_wspd_ds = xr.open_dataset('../../01_data/raw_data/sos_ds_1H_storage.nc')
# SOS data is in utc, let's convert it to mountain time
# First let's add the UTC timezone to the datasets 
sos_1H_max_wspd_ds['time'] = pd.to_datetime(sos_1H_max_wspd_ds.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)
sos_1H_mean_wspd_ds['time'] = pd.to_datetime(sos_1H_mean_wspd_ds.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)


# now let's grab wind data from SAIL in Gothic 
w22_sail_met_qc_ds_1H = xr.open_dataset('../../01_data/processed_data/sail_processed/sail_ds_1H_met_2022.nc')
w23_sail_met_qc_ds_1H = xr.open_dataset('../../01_data/processed_data/sail_processed/sail_ds_1H_met_2023.nc')

# Now we grab the SPLASH data from Avery Picnic and Kettle Ponds

w23_splash_ap_qc_ds_1H = xr.open_dataset("../../01_data/processed_data/splash/w23_splash_ap_qc_1H.nc")
w22_splash_ap_qc_ds_1H = xr.open_dataset("../../01_data/processed_data/splash/w22_splash_ap_qc_1H.nc")
w23_splash_kp_qc_ds_1H = xr.open_dataset("../../01_data/processed_data/splash/w23_splash_kp_qc_1H.nc")
w22_splash_kp_qc_ds_1H = xr.open_dataset("../../01_data/processed_data/splash/w22_splash_kp_qc_1H.nc")

# convert the SPLASH time series to mountain time
w23_splash_ap_qc_ds_1H['time'] = pd.to_datetime(w23_splash_ap_qc_ds_1H.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)
w22_splash_ap_qc_ds_1H['time'] = pd.to_datetime(w22_splash_ap_qc_ds_1H.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)
w23_splash_kp_qc_ds_1H['time'] = pd.to_datetime(w23_splash_kp_qc_ds_1H.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)
w22_splash_kp_qc_ds_1H['time'] = pd.to_datetime(w22_splash_kp_qc_ds_1H.time).tz_localize('UTC').tz_convert('MST').tz_localize(None)

Now let's add precipitation to each dataset for the respective years

In [8]:
# add precipitation data to each years data
# SAIL
w22_sail_met_qc_ds_1H['precip_rate'] = w22_prcp_rate_1H_gts_ds['precip_rate']
w23_sail_met_qc_ds_1H['precip_rate'] = w23_prcp_rate_1H_gts_ds['precip_rate']
# SOS
sos_1H_mean_wspd_ds['precip_rate'] = w23_prcp_rate_1H_mtcb_ds['precip_rate']
# SPLASH
w22_splash_ap_qc_ds_1H['precip_rate'] = w22_prcp_rate_1H_mtcb_ds['precip_rate']
w22_splash_kp_qc_ds_1H['precip_rate'] = w22_prcp_rate_1H_mtcb_ds['precip_rate']
w23_splash_ap_qc_ds_1H['precip_rate'] = w23_prcp_rate_1H_mtcb_ds['precip_rate']
w23_splash_kp_qc_ds_1H['precip_rate'] = w23_prcp_rate_1H_mtcb_ds['precip_rate']

### Plot Wind Speed and Precipitation for 2022 and 2023

In [9]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=w22_prcp_rate_1H_gts_ds.time,
                         y=w22_prcp_rate_1H_gts_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Gothic Townsite'))
fig.update_layout(title='Winter Precipitation (Dec 1 - Mar 31) 2021-2022',
                    xaxis_title='Time',
                    yaxis_title='Precipitation Rate (mm/hr)',
                    # height=600,
                    # width=800
)

# add a second y-axis
fig.update_layout(yaxis2=dict(title='Wind Speed (m/s)',
                              overlaying='y',
                              side='right'))
fig.add_trace(go.Scatter(x=w22_sail_met_qc_ds_1H.time,
                            y=w22_sail_met_qc_ds_1H.wspd_arith_mean,
                            mode='lines',
                            marker=dict(size=5,
                                        color='red'),
                            name='10-m wind gust at Gothic',
                            showlegend=False,
                            yaxis='y2'))
# move the legend up a bit
fig.update_layout(legend=dict(y=1.2))

In [10]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_gts_ds.time,
                         y=w23_prcp_rate_1H_gts_ds.precip_rate,
                         mode='lines',
                         marker=dict(size=5),
                         name='Gothic Townsite'))
fig.update_layout(title='Winter Precipitation (Dec 1 - Mar 31) 2022-2023',
                    xaxis_title='Time',
                    yaxis_title='Precipitation Rate (mm/hr)',
                    # height=600,
                    # width=800
)

# add a second y-axis
fig.update_layout(yaxis2=dict(title='Wind Speed (m/s)',
                              overlaying='y',
                              side='right'))
fig.add_trace(go.Scatter(x=w23_sail_met_qc_ds_1H.time,
                            y=w23_sail_met_qc_ds_1H.wspd_arith_mean,
                            mode='lines',
                            marker=dict(size=5,
                                        color='red'),
                            name='10-m wind gust at Gothic',
                            showlegend=False,
                            yaxis='y2'))
# move the legend up a bit
fig.update_layout(legend=dict(y=1.2))


There appears to be a rise in wind gust speed during stormy periods, but the signal to noise ratio is very low, so not much can be deduced from this

### Scatter plot of wind gusts and precipitation

In [11]:
# let's make a scatter plot next 
fig = go.Figure()
fig.add_trace(go.Scatter(x=w23_prcp_rate_1H_gts_ds.precip_rate,
                         y=w23_sail_met_qc_ds_1H.sel(time=w23_prcp_rate_1H_gts_ds.time).wspd_arith_mean,
                         mode='markers',
                         marker=dict(size=5),
                         ))
fig.update_layout(title='Precipitation Rate vs. 10-m Wind Gust',
                    xaxis_title='Precipitation Rate (mm/hr)',
                    yaxis_title='10-m Wind Gust (m/s)',
                    height=600,
                    width=800
)


Not much here, but we can generally say, when it is snowing, it is often also windy. What about looking at how these variables covary at different lag times?

### Time Lagged Cross-Correlation Plots between Variables

In [12]:
# let's add these two dataset together into a dataframe
w23_prcp_rate_1H_gts_df = w23_prcp_rate_1H_gts_ds.to_dataframe()
w22_prcp_rate_1H_gts_df = w22_prcp_rate_1H_gts_ds.to_dataframe()
# create a binary precipitation dataset for 2022
binary_22_df = w22_prcp_rate_1H_gts_df['precip_rate'].apply(lambda x: 1 if x > 0 else 0)
binary_22_df.name = 'precip_binary'
# create a binary precipitation dataset for 2023
binary_23_df = w23_prcp_rate_1H_gts_df['precip_rate'].apply(lambda x: 1 if x > 0 else 0)
binary_23_df.name = 'precip_binary'
# add blowing snow flux
total_bsf = sos_1H_mean_wspd_ds['SF_avg_1m_ue']+sos_1H_mean_wspd_ds['SF_avg_2m_ue']
# translate the data before transforming it
translated_bsf = total_bsf + 1 - total_bsf.min()
sos_1H_mean_wspd_ds['bsf'] = np.log(translated_bsf).where(sos_1H_mean_wspd_ds['SF_avg_1m_ue']+sos_1H_mean_wspd_ds['SF_avg_2m_ue']>0.001, 0)
# convert to dataframe
sos_1H_mean_wspd_df = sos_1H_mean_wspd_ds.sel(time=w23_prcp_rate_1H_gts_ds.time).to_dataframe()
sail_1H_mean_wspd_22_df = w22_sail_met_qc_ds_1H.to_dataframe()
sail_1H_mean_wspd_23_df = w23_sail_met_qc_ds_1H.to_dataframe()

combined_sos_sail_df = pd.concat([binary_23_df, sos_1H_mean_wspd_df], axis=1)[['precip_binary','spd_10m_uw','bsf','precip_rate','w_h2o__10m_uw']]
combined_sail_23_df = pd.concat([binary_23_df, sail_1H_mean_wspd_23_df], axis=1)[['precip_binary','wspd_arith_mean']]
combined_sail_22_df = pd.concat([binary_22_df, sail_1H_mean_wspd_22_df], axis=1)[['precip_binary','wspd_arith_mean']]

In [13]:
# save the precipitation binary file
binary_23_df.to_csv('../../01_data/processed_data/sail_processed/sail_ld_gothic_2023_precip_binary.csv')

Check for stationarity

In [14]:
from statsmodels.tsa.stattools import adfuller
def adf_test(timeseries):
    dftest = adfuller(timeseries, autolag='AIC')
    result = pd.Series(dftest[0:4], index=['Test Statistic','P-value','Lags Used','No of Observations'])
    for key,value in dftest[4].items():
        result['Critical Value (%s)'%key] = value
    return result
    
# adf_table = df.drop('week', axis = 1)
df = combined_sail_22_df.dropna().apply(adf_test, axis = 0)
df

precip_binary  wspd_arith_mean
Test Statistic        -7.349540e+00    -7.018828e+00
P-value                1.014506e-10     6.624279e-10
Lags Used              1.300000e+01     2.700000e+01
No of Observations     2.885000e+03     2.871000e+03
Critical Value (1%)   -3.432619e+00    -3.432630e+00
Critical Value (5%)   -2.862542e+00    -2.862547e+00
Critical Value (10%)  -2.567304e+00    -2.567306e+00

### Cross-correlation Plots

Here I used the pointbiserialr function to calculate the correlation coefficient, which is used when one variable is bivariate and the other is continuous. Using this function did not change the results.


Cross-correlation for 2022 and 2023 between SAIL wind and SAIL Precipitation and for 2023 between SOS wind and SAIL precipitation

In [15]:
# function to create lags
def lagged_cross_corr(df, max_lag, var1, var2, binary=False):
    # Calculate cross-correlation
    lags = np.arange(-max_lag-1, max_lag + 1)
    cross_corr = []
    for lag in lags:
        if binary:
            if lag < 0:
                cross_corr.append(stats.pointbiserialr(df.dropna()[var1].iloc[:lag], df.dropna()[var2].shift(lag).iloc[:lag])[0])
            else:
                cross_corr.append(stats.pointbiserialr(combined_sail_22_df.dropna()[var1].iloc[lag:], combined_sail_22_df.dropna()[var2].shift(lag).iloc[lag:])[0])
        else:
            cross_corr = [df[var1].corr(df[var2].shift(lag)) for lag in lags]
    return lags, cross_corr

In [16]:
# Calculate cross-correlation
lags_sail_22, cross_corr_sail_22 = lagged_cross_corr(combined_sail_22_df, 24, 'wspd_arith_mean', 'precip_binary', binary=True)
lags_sail_23, cross_corr_sail_23 = lagged_cross_corr(combined_sail_23_df, 24, 'wspd_arith_mean', 'precip_binary', binary=False)
lags_sos_23, cross_corr_sos_23 = lagged_cross_corr(combined_sos_sail_df, 24, 'spd_10m_uw', 'precip_binary', binary=False)

# Create plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=lags_sail_22, y=cross_corr_sail_22, mode='lines+markers', name='SAIL 2022'))
fig.add_trace(go.Scatter(x=lags_sail_23, y=cross_corr_sail_23, mode='lines+markers', name='SAIL 2023'))
fig.add_trace(go.Scatter(x=lags_sos_23, y=cross_corr_sos_23, mode='lines+markers', name='SOS 2023'))

fig.update_layout(
    title='Time-Lagged Cross-Correlation between Wind Speed and Precipitation' ,
    xaxis_title='Lag (hours)',
    yaxis_title='Cross-Correlation',
    xaxis=dict(range=[-24.25, 24.25],
               tickmode='linear',
               dtick=6,
               tickfont=dict(size=18)),
    yaxis=dict(range=[-0.5, 0.5], tickfont=dict(size=20)),
    width=800,
    height=600
)
# increase yaxis font label size
fig.update_yaxes(title_font=dict(size=20))
fig.update_xaxes(title_font=dict(size=18),
                # show every 6th tick on the x-axis
                )
# update legend with title and font size
fig.update_layout(legend_title_text='Wind Speed + Precipitation', 
                legend=dict(
                             yanchor="bottom",
                             y=0.01,
                             xanchor="right",
                             x=0.99
                            ))

fig.show()


Cross-correlation between SOS wind speed and SOS blowing snow flux. Also, cross correlation between SOS blowing snow flux and SAIL precipitation

In [17]:
# Calculate cross-correlation
lags_bsf_wspd, cross_corr_bsf_wspd = lagged_cross_corr(combined_sos_sail_df, 24, 'bsf', 'spd_10m_uw', binary=False)
lags_bsf_h2o, cross_corr_bsf_h2o = lagged_cross_corr(combined_sos_sail_df, 24, 'bsf', 'w_h2o__10m_uw', binary=False)
lags_bsf_prcp, cross_corr_bsf_prcp = lagged_cross_corr(combined_sos_sail_df, 24, 'bsf', 'precip_rate', binary=False)

# Create plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=lags_bsf_wspd, y=cross_corr_bsf_wspd, mode='lines+markers', name='BSF + WSPD'))
fig.add_trace(go.Scatter(x=lags_bsf_h2o, y=cross_corr_bsf_h2o, mode='lines+markers', name='BSF + H2O Flux'))
fig.add_trace(go.Scatter(x=lags_bsf_prcp, y=cross_corr_bsf_prcp, mode='lines+markers', name='BSF + PRCP'))

fig.update_layout(
    title='Time-Lagged Cross-Correlation for Blowing Snow Flux' ,
    xaxis_title='Lag (hours)',
    yaxis_title='Cross-Correlation',
    xaxis=dict(range=[-24.25, 24.25],
               tickmode='linear',
               dtick=6,
               tickfont=dict(size=18)),
    yaxis=dict(range=[-0.5, 0.5], tickfont=dict(size=20)),
    width=800,
    height=600
)
# increase yaxis font label size
fig.update_yaxes(title_font=dict(size=20))
fig.update_xaxes(title_font=dict(size=18),
                # show every 6th tick on the x-axis
                )
# update legend with title and font size
fig.update_layout(legend_title_text='Legend', 
                legend=dict(
                             yanchor="bottom",
                             y=0.01,
                             xanchor="right",
                             x=0.99
                            ))

fig.show()


In [18]:
# Calculate cross-correlation
# max_lag = 24
lags = np.arange(-72,30,6)
max_lag = 72
lags = np.arange(-max_lag-1, max_lag + 1)
# cross_corr = []
# for lag in lags:
#     if lag < 0:
#         cross_corr.append(stats.pointbiserialr((combined_sos_sail_df).dropna()['bsf'].iloc[:lag], combined_sos_sail_df.dropna()['precip_binary'].shift(lag).iloc[:lag])[0])
#     else:
#         cross_corr.append(stats.pointbiserialr((combined_sos_sail_df).dropna()['bsf'].iloc[lag:], combined_sos_sail_df.dropna()['precip_binary'].shift(lag).iloc[lag:])[0])
cross_corr = [combined_sos_sail_df['w_h2o__10m_uw'].corr(combined_sos_sail_df['precip_rate'].shift(lag)) for lag in lags]
# Create plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=lags, y=cross_corr, mode='lines+markers', name='Cross-correlation'))

fig.update_layout(
    title='Time-Lagged Cross-Correlation between Vertical Water Vapor Flux and Precipitation' ,
    xaxis_title='Lag (hours)',
    yaxis_title='Cross-Correlation',
    xaxis=dict(range=[-72,24],
               tickmode='linear',
               tickfont=dict(size=18),
               # show ticks evey 6 units
                dtick=6),
    yaxis=dict(range=[-0.4, 0.4], tickfont=dict(size=20)),
    width=1000,
    height=600
)
# increase yaxis font label size
fig.update_yaxes(title_font=dict(size=20))
fig.update_xaxes(title_font=dict(size=18))

fig.show()


### Tilden Precipitation if wanted

In [29]:
fn_2022 = "/storage/elilouis/sublimationofsnow/tilden_precip_data/KP22_274-365.PRECIP1"
fn_2023 = "/storage/elilouis/sublimationofsnow/tilden_precip_data/KP23_001-177.PRECIP1"

df = pd.concat([
    pd.read_csv(fn_2022, delim_whitespace=True),
    pd.read_csv(fn_2023, delim_whitespace=True)
])
# create timestamps from strings
df['date'] = pd.to_datetime(df['date'])
# calculate accumulated precip
# combine data and time(MST) columns into a single datetime column
df['datetime'] = pd.to_datetime(df['date'].astype(str) + ' ' + df['time(MST)'].astype(str))
# set the datetime to the index
df = df.set_index('datetime', drop=True)
# sort index
df = df.sort_index()

In [31]:
# save tilden data
# df.to_csv('../../01_data/processed_data/splash/tilden_precip_2022_2023.csv')

# Linear Relationships between Variables

### Filtering days with snow in the past 24 hours and days with no snow in the past 24 hours

Is the relationship between wind speed and blowing snow flux stronger if it precipitated?

### Plotting Wind Direction

In [25]:
# Add blowing snow flux 
max_val = sos_1H_max_wspd_ds['w_h2o__3m_uw'].mean()+(sos_1H_max_wspd_ds['w_h2o__3m_uw'].std()*3)
min_val = sos_1H_max_wspd_ds['w_h2o__3m_uw'].mean()-(sos_1H_max_wspd_ds['w_h2o__3m_uw'].std()*3)
sos_1H_max_wspd_ds['bsf'] = np.log(sos_1H_max_wspd_ds['SF_avg_1m_ue']+sos_1H_max_wspd_ds['SF_avg_2m_ue']).where(sos_1H_max_wspd_ds['SF_avg_1m_ue']+sos_1H_max_wspd_ds['SF_avg_2m_ue']>0.001)
# Filter
filtered_ds = sos_1H_max_wspd_ds.where((sos_1H_max_wspd_ds['w_h2o__3m_uw']<max_val) &
                                          (sos_1H_max_wspd_ds['w_h2o__3m_uw']>min_val)
                                            #  (sos_1H_max_wspd_ds['spd_10m_ue']>=5)
                                          )

binary_23_daily_df = binary_23_df.resample('1D').sum()
binary_23_3D_df = binary_23_df.resample('3D').sum()
# if precip binary is > 1, set to 1
binary_23_daily_df = binary_23_daily_df.apply(lambda x: 1 if x > 3 else 0)
binary_23_3D_df = binary_23_3D_df.apply(lambda x: 1 if x > 3 else 0)
binary_23_hourly_df = binary_23_daily_df.resample('1H').ffill()
binary_23_3D_hourly_df = binary_23_3D_df.resample('1H').ffill()

start_date = '2023-03-01'
end_date = '2023-03-31'
# add to the ds 
sos_1H_max_wspd_no_prcp = filtered_ds.sel(time=binary_23_df.iloc[:-7][binary_23_df==0].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_prcp = filtered_ds.sel(time=binary_23_df.iloc[:-7][binary_23_df==1].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_no_1D_prcp = filtered_ds.sel(time=binary_23_hourly_df.iloc[:-7][binary_23_hourly_df==0].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_3D_prcp = filtered_ds.sel(time=binary_23_3D_hourly_df.iloc[:-7][binary_23_3D_hourly_df==0].index).sel(time=slice(start_date, end_date))

def create_linreg(ds, x, y):
   tmp_ds = ds[[x,y]].dropna(dim='time')  
   slope, intercept, r,_,_ = stats.linregress(tmp_ds[x],tmp_ds[y])
   x_pred = np.array([tmp_ds[x].min(), tmp_ds[x].max()])
   y_pred = slope*x_pred + intercept
   return x_pred, y_pred, round(r**2,2)
if sos_1H_max_wspd_3D_prcp.time.size == 0:
   skip = True
else:
    skip = False 
    
# create linear regression for each dataset
x1, fit_1, r2_1 = create_linreg(sos_1H_max_wspd_no_prcp, 'spd_10m_ue', 'bsf')
x2, fit_2, r2_2 = create_linreg(sos_1H_max_wspd_prcp, 'spd_10m_ue', 'bsf')
x3, fit_3, r2_3 = create_linreg(sos_1H_max_wspd_no_1D_prcp, 'spd_10m_ue', 'bsf')
if not skip:
    x4, fit_4, r2_4 = create_linreg(sos_1H_max_wspd_3D_prcp, 'spd_10m_ue', 'bsf')
else:
    r2_4 = 'NaN'
    

# make a plotly plot with 2 rows and 2 columns
fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.1,
                    subplot_titles=(f"Periods with No Precipitation - R2={r2_1}", 
                                    f"Periods with Precipitation - R2={r2_2}",
                                    f"Periods with No Precipitation<br>for previous 24 Hours - R2={r2_3}", 
                                    f"Periods with No Precipitation<br>for previous 72 Hours - R2={r2_4}"))

# add the first plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_no_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_no_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_no_prcp.dir_10m_ue, #set color equal to a variable
                                     colorscale='twilight_r', # one of plotly colorscales
                                     showscale=True),
                         name='Blowing Snow Flux',
                         showlegend=False,
                         ),
                         row=1, col=1)
fig.add_trace(go.Scatter(x=x1, 
                        y=fit_1, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=1, col=1)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_1}",
    ]), col=1, row=1
)

# add the second plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_prcp.dir_10m_ue, #set color equal to a variable
                                     colorscale='twilight_r', # one of plotly colorscales
                                     showscale=False),
                         showlegend=False),
                         row=1, col=2)
fig.add_trace(go.Scatter(x=x2, 
                        y=fit_2, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=1, col=2)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_2}",
    ]), col=2, row=1
)


# add the third plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_no_1D_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_no_1D_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_no_1D_prcp.dir_10m_ue, #set color equal to a variable
                                     colorscale='twilight_r', # one of plotly colorscales
                                     showscale=False),
                         showlegend=False),
                         row=2, col=1)
fig.add_trace(go.Scatter(x=x3, 
                        y=fit_3, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=2, col=1)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_3}",
    ]), col=1, row=2
)
                        
if not skip:
    # add the fourth plot
    fig.add_trace(go.Scatter(x=sos_1H_max_wspd_3D_prcp.spd_10m_ue,
                            y=sos_1H_max_wspd_3D_prcp.bsf,
                            mode='markers',
                            marker=dict(size=10,
                                        color=sos_1H_max_wspd_3D_prcp.dir_10m_ue, #set color equal to a variable
                                        colorscale='twilight_r', # one of plotly colorscales
                                        showscale=False),
                            showlegend=False),
                            row=2, col=2,)
    fig.add_trace(go.Scatter(x=x4, 
                            y=fit_4, 
                            mode='lines', 
                            name='Linear Regression', 
                            showlegend=False),
                            row=2, col=2)
    # add hover with r2_1
    fig.update_traces(marker_line_width=1,
                    marker_line_color="black",
                    hovertemplate="<br>".join([f"R2: {r2_4}",]), 
                    col=2, row=2)                                         

# format the size, axis titles, and subplot titles
fig.update_layout(height=800,
                width=800,
                title_text=f"Hourly Blowing Snow Flux vs. Max Wind Speed<br>{start_date} - {end_date}",
                xaxis3_title="Wind Speed (m/s)",
                xaxis4_title="Wind Speed (m/s)",
                yaxis_title="Blowing Snow Flux",
                yaxis3_title="Blowing Snow Flux",
                coloraxis_colorbar=dict(
                title="Wind Direction (deg&;)"),
)
fig.update_traces(marker_line_width=1,
                  marker_line_color="black")
fig.update_xaxes(title_font_size=20)
fig.update_yaxes(title_font_size=20, range=[-7,1])


divide by zero encountered in log


### Plotting 3m C temperature

In [22]:
# Add blowing snow flux 
max_val = sos_1H_max_wspd_ds['w_h2o__3m_uw'].mean()+(sos_1H_max_wspd_ds['w_h2o__3m_uw'].std()*3)
min_val = sos_1H_max_wspd_ds['w_h2o__3m_uw'].mean()-(sos_1H_max_wspd_ds['w_h2o__3m_uw'].std()*3)
sos_1H_max_wspd_ds['bsf'] = np.log(sos_1H_max_wspd_ds['SF_avg_1m_ue']+sos_1H_max_wspd_ds['SF_avg_2m_ue']).where(sos_1H_max_wspd_ds['SF_avg_1m_ue']+sos_1H_max_wspd_ds['SF_avg_2m_ue']>0.001)
# Filter
filtered_ds = sos_1H_max_wspd_ds.where((sos_1H_max_wspd_ds['w_h2o__3m_uw']<max_val) &
                                          (sos_1H_max_wspd_ds['w_h2o__3m_uw']>min_val)
                                            #  (sos_1H_max_wspd_ds['spd_10m_ue']>=5)
                                          )

binary_23_daily_df = binary_23_df.resample('1D').sum()
binary_23_3D_df = binary_23_df.resample('3D').sum()
# if precip binary is > 1, set to 1
binary_23_daily_df = binary_23_daily_df.apply(lambda x: 1 if x > 3 else 0)
binary_23_3D_df = binary_23_3D_df.apply(lambda x: 1 if x > 3 else 0)
binary_23_hourly_df = binary_23_daily_df.resample('1H').ffill()
binary_23_3D_hourly_df = binary_23_3D_df.resample('1H').ffill()

start_date = '2022-12-01'
end_date = '2022-12-31'
# add to the ds 
sos_1H_max_wspd_no_prcp = filtered_ds.sel(time=binary_23_df.iloc[:-7][binary_23_df==0].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_prcp = filtered_ds.sel(time=binary_23_df.iloc[:-7][binary_23_df==1].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_no_1D_prcp = filtered_ds.sel(time=binary_23_hourly_df.iloc[:-7][binary_23_hourly_df==0].index).sel(time=slice(start_date, end_date))
sos_1H_max_wspd_3D_prcp = filtered_ds.sel(time=binary_23_3D_hourly_df.iloc[:-7][binary_23_3D_hourly_df==0].index).sel(time=slice(start_date, end_date))

if sos_1H_max_wspd_3D_prcp.time.size == 0:
   skip = True
else:
    skip = False
def create_linreg(ds, x, y):
   tmp_ds = ds[[x,y]].dropna(dim='time')  
   slope, intercept, r,_,_ = stats.linregress(tmp_ds[x],tmp_ds[y])
   x_pred = np.array([tmp_ds[x].min(), tmp_ds[x].max()])
   y_pred = slope*x_pred + intercept
   return x_pred, y_pred, round(r**2,2)

# create linear regression for each dataset
x1, fit_1, r2_1 = create_linreg(sos_1H_max_wspd_no_prcp, 'spd_10m_ue', 'bsf')
x2, fit_2, r2_2 = create_linreg(sos_1H_max_wspd_prcp, 'spd_10m_ue', 'bsf')
x3, fit_3, r2_3 = create_linreg(sos_1H_max_wspd_no_1D_prcp, 'spd_10m_ue', 'bsf')
if not skip:
    x4, fit_4, r2_4 = create_linreg(sos_1H_max_wspd_3D_prcp, 'spd_10m_ue', 'bsf')


# make a plotly plot with 2 rows and 2 columns
fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.1,
                    subplot_titles=(f"Periods with No Precipitation - R2={r2_1}", 
                                    f"Periods with Precipitation - R2={r2_2}",
                                    f"Periods with No Precipitation<br>for previous 24 Hours - R2={r2_3}", 
                                    f"Periods with No Precipitation<br>for previous 72 Hours - R2={r2_4}"))

# add the first plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_no_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_no_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_no_prcp.T_3m_c, #set color equal to a variable
                                     colorscale='viridis', # one of plotly colorscales
                                     cmin=-12,
                                     cmax=0,
                                     showscale=True),
                         name='Blowing Snow Flux',
                         showlegend=False,
                         ),
                         row=1, col=1)
fig.add_trace(go.Scatter(x=x1, 
                        y=fit_1, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=1, col=1)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_1}",
    ]), col=1, row=1
)

# add the second plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_prcp.T_3m_c, #set color equal to a variable
                                     colorscale='viridis', # one of plotly colorscales
                                     cmin=-12,
                                     cmax=0,
                                     showscale=False),
                         showlegend=False),
                         row=1, col=2)
fig.add_trace(go.Scatter(x=x2, 
                        y=fit_2, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=1, col=2)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_2}",
    ]), col=2, row=1
)


# add the third plot
fig.add_trace(go.Scatter(x=sos_1H_max_wspd_no_1D_prcp.spd_10m_ue,
                         y=sos_1H_max_wspd_no_1D_prcp.bsf,
                         mode='markers',
                         marker=dict(size=10,
                                     color=sos_1H_max_wspd_no_1D_prcp.T_3m_c, #set color equal to a variable
                                     colorscale='viridis', # one of plotly colorscales
                                     cmin=-12,
                                     cmax=0,
                                     showscale=False),
                         showlegend=False),
                         row=2, col=1)
fig.add_trace(go.Scatter(x=x3, 
                        y=fit_3, 
                        mode='lines', 
                        name='Linear Regression', 
                        showlegend=False),
                        row=2, col=1)
# add hover with r2_1
fig.update_traces(
    hovertemplate="<br>".join([
        f"R2: {r2_3}",
    ]), col=1, row=2
)                         
if not skip:
    # add the fourth plot
    fig.add_trace(go.Scatter(x=sos_1H_max_wspd_3D_prcp.spd_10m_ue,
                            y=sos_1H_max_wspd_3D_prcp.bsf,
                            mode='markers',
                            marker=dict(size=10,
                                        color=sos_1H_max_wspd_3D_prcp.T_3m_c, #set color equal to a variable
                                        colorscale='viridis', # one of plotly colorscales
                                        cmin=-12,
                                        cmax=0,
                                        showscale=False),
                            showlegend=False),
                            row=2, col=2,)
    fig.add_trace(go.Scatter(x=x4, 
                            y=fit_4, 
                            mode='lines', 
                            name='Linear Regression', 
                            showlegend=False),
                            row=2, col=2)
    # add hover with r2_1
    fig.update_traces(marker_line_width=1,
                    marker_line_color="black",
                    hovertemplate="<br>".join([f"R2: {r2_4}",]), 
                    col=2, row=2)                                         

# format the size, axis titles, and subplot titles
fig.update_layout(height=800,
                width=800,
                title_text=f"Hourly log(Blowing Snow Flux) vs. Max Wind Speed<br>{start_date} - {end_date}",
                xaxis3_title="Wind Speed (m/s)",
                xaxis4_title="Wind Speed (m/s)",
                yaxis_title="log(Blowing Snow Flux)",
                yaxis3_title="log(Blowing Snow Flux)",
                coloraxis_colorbar=dict(
                title="Wind Direction (deg&;)"),
)
fig.update_traces(marker_line_width=1,
                  marker_line_color="black")
fig.update_xaxes(title_font_size=20)
fig.update_yaxes(title_font_size=20, range=[-7,1])


divide by zero encountered in log


### Make Heatmaps Precipitation with Wind Speed and Direction

In [23]:
# function for prepping the data
def make_heatmap_df(ds, location, campaign, year, max_spd=False):
    if campaign == 'sail':
        if max_spd == True:
            wspd_var = 'wspd_max'
            wdir_var = 'wdir_max'
        else:
            wspd_var = 'wspd_arith_mean'
            wdir_var = 'wdir_vec_mean'
        title = 'Gothic'
    elif campaign =='sos':
        if max_spd == True:
            wspd_var = 'wspd_max'
            wdir_var = 'wdir_max'
        else:
            wspd_var = 'spd_10m_uw'
            wdir_var = 'dir_10m_uw'
        temp_var = 'T_3m_c'
        title = 'Kettle Ponds'
    else:
        if max_spd == True:
            wspd_var = 'wspd_max'
            wdir_var = 'wdir_max'
        else:
            wspd_var = 'wspd_vec_mean'
            wdir_var = 'wdir_vec_mean'
        temp_var = 'temp'
        if location == 'kp':
            title = 'Kettle Ponds'
        else: title = 'Avery Picnic'
    precip_var = 'precip_rate'
    df_to_use = ds.to_dataframe()
    df_test = df_to_use[[wspd_var, wdir_var, precip_var]]

    # wind speed bins
    wspd_bins = [0, 2, 4, 6, 8, 10,]
    # wind direction bins
    wdir_bins = [0, 45, 90, 135, 180, 225, 270, 315, 360]

    # wspd cut and sum sublimation for each bin
    wsp_assignment = pd.cut(df_test[wspd_var], bins=wspd_bins, labels=wspd_bins[:-1])
    wsp_assignment.name = 'wsp_assignment'
    # wdir cut and sum sublimation for each bin
    wdir_assignment = pd.cut(df_test[wdir_var], bins=wdir_bins, labels=wdir_bins[:-1])
    wdir_assignment.name = 'wdir_assignment'

    # combine the two assignments and the sublimation
    df_test['wsp_assignment'] = wsp_assignment.values
    df_test['wdir_assignment'] = wdir_assignment.values

    # groupby the wspd and wdir assignments and get the sum of w_h2o__3m_uw
    grouped = df_test.groupby(['wsp_assignment', 'wdir_assignment']).sum()[precip_var]
    # unstack and put into a dataframe
    grouped =(grouped.unstack())
    grouped = 100*(grouped/(grouped.sum().sum()))

    # plot grouped as a heatmap
    fig = go.Figure()
    fig.add_trace(go.Heatmap(z=grouped.values, 
                            x=grouped.columns, 
                            y=grouped.index,

                            colorbar={'title':'% of total <br>precipitation'},
                            colorscale='Blues',
                            # min and max color values
                            zmin=0,
                            zmax=20,
                            xgap=1,
                            ygap=1,
                            ))
    # add grid
    fig.update_layout(height=400, 
                    width=600,
                    xaxis_title='Wind Direction',
                    yaxis_title='Wind Speed',
                    title=f'Wind Speed and Wind Direction with Precipitation<br> for {campaign.upper()} in {year} at {title}',
                    )
    # change x-axis ticks to be cardinal wind directions
    fig.update_xaxes(tickvals=[0, 45, 90, 135, 180, 225, 270, 315], ticktext=['N', 'NE', 'E', 'SE', 'S', 'SW', 'W', 'NW'])
    # update y-axes ticks to be wind speed bins
    fig.update_yaxes(tickvals=[0, 2, 4, 6, 8, 10, 12, 14, 16, 18], ticktext=['0-2', '2-4', '4-6', '6-8', '8-10', '10-12', '12-14', '14-16', '16-18', '18-20'])
    # save the figure as a png
    pio.write_image(fig,f'../../04_products/figures/sandbox/{campaign}_{location}_{year}_ppt_winds.png', scale=8)
    return fig


### 2022

In [267]:
make_heatmap_df(w22_sail_met_qc_ds_1H, 
                location='gts',
                campaign = 'sail',
                year='2022')

# update legend title to legend_title='Percent of Winter Sublimation (%)'

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


In [268]:
make_heatmap_df(w22_splash_ap_qc_ds_1H, 
                location='ap',
                campaign = 'splash',
                year='2022')

# update legend title to legend_title='Percent of Winter Sublimation (%)'

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


In [269]:
make_heatmap_df(w22_splash_kp_qc_ds_1H, 
                location='kp',
                campaign = 'splash',
                year='2022')

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


2023

In [270]:
make_heatmap_df(w23_splash_ap_qc_ds_1H, 
                location='ap',
                campaign = 'splash',
                year='2023')

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


In [271]:
make_heatmap_df(w23_splash_kp_qc_ds_1H, 
                location='kp',
                campaign = 'splash',
                year='2023')

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


In [272]:
make_heatmap_df(sos_1H_mean_wspd_ds, 
                location='kp',
                campaign = 'sos',
                year='2023')

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


In [273]:
make_heatmap_df(w23_sail_met_qc_ds_1H, 
                location='gts',
                campaign = 'sail',
                year='2023')


The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
